In [20]:
#Importing required python libraries

import pandas as pd
import numpy as np
import scipy.sparse as sparse
from scipy.sparse.linalg import spsolve
from sklearn.preprocessing import MinMaxScaler

books_df = pd.read_csv('/home/sovaniakshay/Documents/Books.csv',engine='python',sep=',')
books_df = books_df.rename(columns = {'ISBN;"Book-Title";"Book-Author";"Year-Of-Publication";"Publisher";"Image-URL-S";"Image-URL-M";"Image-URL-L"':'ISBN'})
books_df['book_title'] = books_df['ISBN'].str.split(';').str[1]
books_df['ISBN'] = books_df['ISBN'].str.split(';').str[0]
new_books_df = books_df[['book_title','ISBN']].drop_duplicates()
ratings_df = pd.read_csv("/home/sovaniakshay/Documents/CS512/Book-Ratings.csv", error_bad_lines=False)

merged_books_df = pd.merge(ratings_df,new_books_df,on='ISBN')
merged_books_df['ISBN_id'] = merged_books_df['ISBN'].astype("category").cat.codes
merged_books_df['USER_id'] = merged_books_df['User-ID'].astype("category").cat.codes

books_lookup = merged_books_df[['ISBN_id','book_title']].drop_duplicates()
books_lookup['ISBN_id'] = books_lookup.ISBN_id.astype(str)

merged_books_df.columns = ['User_ID','ISBN','Book_Rating','Book_Title','ISBN_ID','USER_id']

#full_data_books is a dataframe having complete information about book name, ID, userID.  
full_data_books = merged_books_df.copy()


merged_books_df = merged_books_df.drop(['User_ID','ISBN','Book_Title'],axis=1)
input_data_for_matrix = merged_books_df.loc[merged_books_df.Book_Rating != 0]

users = list(np.sort(input_data_for_matrix['USER_id'].unique()))
ISBN = list(np.sort(input_data_for_matrix['ISBN_ID'].unique()))
rating = list(input_data_for_matrix['Book_Rating'])
rows = input_data_for_matrix['USER_id'].astype(int)
cols = input_data_for_matrix['ISBN_ID'].astype(int)

ratings_matrix=sparse.csr_matrix((rating,(rows,cols)),shape = (len(rows),len(cols)))


In [3]:

#Details of the generated ratings sparse matrix 

print(ratings_matrix.data)
print(ratings_matrix.nnz)

[ 5.  5.  6. ... 10.  7.  7.]
73771


In [3]:
# ALS function generates 2 vectors X and Y. one for User_features and the other for items_features

def ALS(ratings_matrix,alpha,iterations,lambda_val,features):
    confidence_matrix = ratings_matrix * alpha
    
    user_size,book_size = ratings_matrix.shape
    print(user_size)
    print(book_size)
    X = sparse.csr_matrix(np.random.normal(size = (user_size,features)))
    Y = sparse.csr_matrix(np.random.normal(size = (book_size,features)))
    
    X_I = sparse.eye(user_size)
    Y_I = sparse.eye(book_size)
    
    I = sparse.eye(features)
    lI = lambda_val * I
    u_iteration = 0
    i_iteration = 0
    for i in range(iterations):
        #Update the two vectors X and Y which are respectively for users and books for 'iteration' number of iterations.
        print ('itearation %d of total %d iterations' % (i+1,iterations))
        
        yTy = Y.T.dot(Y)
        xTx = X.T.dot(X)
        
        for u in range(user_size):
            u_iteration += 1
            print('In U for the %d time' % (u_iteration))
            u_row = confidence_matrix[u,:].toarray() 

            p_u = u_row.copy()
            p_u[p_u != 0] = 1.0

            CuI = sparse.diags(u_row, [0])
            Cu = CuI + Y_I

            yT_CuI_y = Y.T.dot(CuI).dot(Y)
            yT_Cu_pu = Y.T.dot(Cu).dot(p_u.T)
            X[u] = spsolve(yTy + yT_CuI_y + lI, yT_Cu_pu)
            #This is one row updation of of the user vectors

    
        for i in range(book_size):
            i_iteration += 1
            print('In I for the %d time' % (i_iteration))
            i_row = confidence_matrix[:,i].T.toarray()

            p_i = i_row.copy()
            p_i[p_i != 0] = 1.0

            CiI = sparse.diags(i_row, [0])
            Ci = CiI + X_I

            xT_CiI_x = X.T.dot(CiI).dot(X)
            xT_Ci_pi = X.T.dot(Ci).dot(p_i.T)
            Y[i] = spsolve(xTx + xT_CiI_x + lI, xT_Ci_pi)
            #This is one column updation of of the book vectors
    print('Vectores X and Y have been created')
    return X, Y
    #in the end, we return the two vectors X and Y based on which recommendations are to be done
        
    

In [4]:
X,Y = ALS(ratings_matrix,40,1,0.1,10)

73771
73771
itearation 1 of total 1 iterations
In U for the 1 time
In U for the 2 time
In U for the 3 time
In U for the 4 time
In U for the 5 time
In U for the 6 time
In U for the 7 time
In U for the 8 time
In U for the 9 time
In U for the 10 time
In U for the 11 time
In U for the 12 time
In U for the 13 time
In U for the 14 time
In U for the 15 time
In U for the 16 time
In U for the 17 time
In U for the 18 time
In U for the 19 time
In U for the 20 time
In U for the 21 time
In U for the 22 time
In U for the 23 time
In U for the 24 time
In U for the 25 time
In U for the 26 time
In U for the 27 time
In U for the 28 time
In U for the 29 time
In U for the 30 time
In U for the 31 time
In U for the 32 time
In U for the 33 time
In U for the 34 time
In U for the 35 time
In U for the 36 time
In U for the 37 time
In U for the 38 time
In U for the 39 time
In U for the 40 time
In U for the 41 time
In U for the 42 time
In U for the 43 time
In U for the 44 time
In U for the 45 time
In U for the 46 t

In U for the 378 time
In U for the 379 time
In U for the 380 time
In U for the 381 time
In U for the 382 time
In U for the 383 time
In U for the 384 time
In U for the 385 time
In U for the 386 time
In U for the 387 time
In U for the 388 time
In U for the 389 time
In U for the 390 time
In U for the 391 time
In U for the 392 time
In U for the 393 time
In U for the 394 time
In U for the 395 time
In U for the 396 time
In U for the 397 time
In U for the 398 time
In U for the 399 time
In U for the 400 time
In U for the 401 time
In U for the 402 time
In U for the 403 time
In U for the 404 time
In U for the 405 time
In U for the 406 time
In U for the 407 time
In U for the 408 time
In U for the 409 time
In U for the 410 time
In U for the 411 time
In U for the 412 time
In U for the 413 time
In U for the 414 time
In U for the 415 time
In U for the 416 time
In U for the 417 time
In U for the 418 time
In U for the 419 time
In U for the 420 time
In U for the 421 time
In U for the 422 time
In U for t

In U for the 762 time
In U for the 763 time
In U for the 764 time
In U for the 765 time
In U for the 766 time
In U for the 767 time
In U for the 768 time
In U for the 769 time
In U for the 770 time
In U for the 771 time
In U for the 772 time
In U for the 773 time
In U for the 774 time
In U for the 775 time
In U for the 776 time
In U for the 777 time
In U for the 778 time
In U for the 779 time
In U for the 780 time
In U for the 781 time
In U for the 782 time
In U for the 783 time
In U for the 784 time
In U for the 785 time
In U for the 786 time
In U for the 787 time
In U for the 788 time
In U for the 789 time
In U for the 790 time
In U for the 791 time
In U for the 792 time
In U for the 793 time
In U for the 794 time
In U for the 795 time
In U for the 796 time
In U for the 797 time
In U for the 798 time
In U for the 799 time
In U for the 800 time
In U for the 801 time
In U for the 802 time
In U for the 803 time
In U for the 804 time
In U for the 805 time
In U for the 806 time
In U for t

In U for the 1132 time
In U for the 1133 time
In U for the 1134 time
In U for the 1135 time
In U for the 1136 time
In U for the 1137 time
In U for the 1138 time
In U for the 1139 time
In U for the 1140 time
In U for the 1141 time
In U for the 1142 time
In U for the 1143 time
In U for the 1144 time
In U for the 1145 time
In U for the 1146 time
In U for the 1147 time
In U for the 1148 time
In U for the 1149 time
In U for the 1150 time
In U for the 1151 time
In U for the 1152 time
In U for the 1153 time
In U for the 1154 time
In U for the 1155 time
In U for the 1156 time
In U for the 1157 time
In U for the 1158 time
In U for the 1159 time
In U for the 1160 time
In U for the 1161 time
In U for the 1162 time
In U for the 1163 time
In U for the 1164 time
In U for the 1165 time
In U for the 1166 time
In U for the 1167 time
In U for the 1168 time
In U for the 1169 time
In U for the 1170 time
In U for the 1171 time
In U for the 1172 time
In U for the 1173 time
In U for the 1174 time
In U for th

In U for the 1490 time
In U for the 1491 time
In U for the 1492 time
In U for the 1493 time
In U for the 1494 time
In U for the 1495 time
In U for the 1496 time
In U for the 1497 time
In U for the 1498 time
In U for the 1499 time
In U for the 1500 time
In U for the 1501 time
In U for the 1502 time
In U for the 1503 time
In U for the 1504 time
In U for the 1505 time
In U for the 1506 time
In U for the 1507 time
In U for the 1508 time
In U for the 1509 time
In U for the 1510 time
In U for the 1511 time
In U for the 1512 time
In U for the 1513 time
In U for the 1514 time
In U for the 1515 time
In U for the 1516 time
In U for the 1517 time
In U for the 1518 time
In U for the 1519 time
In U for the 1520 time
In U for the 1521 time
In U for the 1522 time
In U for the 1523 time
In U for the 1524 time
In U for the 1525 time
In U for the 1526 time
In U for the 1527 time
In U for the 1528 time
In U for the 1529 time
In U for the 1530 time
In U for the 1531 time
In U for the 1532 time
In U for th

...

In I for the 72186 time
In I for the 72187 time
In I for the 72188 time
In I for the 72189 time
In I for the 72190 time
In I for the 72191 time
In I for the 72192 time
In I for the 72193 time
In I for the 72194 time
In I for the 72195 time
In I for the 72196 time
In I for the 72197 time
In I for the 72198 time
In I for the 72199 time
In I for the 72200 time
In I for the 72201 time
In I for the 72202 time
In I for the 72203 time
In I for the 72204 time
In I for the 72205 time
In I for the 72206 time
In I for the 72207 time
In I for the 72208 time
In I for the 72209 time
In I for the 72210 time
In I for the 72211 time
In I for the 72212 time
In I for the 72213 time
In I for the 72214 time
In I for the 72215 time
In I for the 72216 time
In I for the 72217 time
In I for the 72218 time
In I for the 72219 time
In I for the 72220 time
In I for the 72221 time
In I for the 72222 time
In I for the 72223 time
In I for the 72224 time
In I for the 72225 time
In I for the 72226 time
In I for the 722

In I for the 72534 time
In I for the 72535 time
In I for the 72536 time
In I for the 72537 time
In I for the 72538 time
In I for the 72539 time
In I for the 72540 time
In I for the 72541 time
In I for the 72542 time
In I for the 72543 time
In I for the 72544 time
In I for the 72545 time
In I for the 72546 time
In I for the 72547 time
In I for the 72548 time
In I for the 72549 time
In I for the 72550 time
In I for the 72551 time
In I for the 72552 time
In I for the 72553 time
In I for the 72554 time
In I for the 72555 time
In I for the 72556 time
In I for the 72557 time
In I for the 72558 time
In I for the 72559 time
In I for the 72560 time
In I for the 72561 time
In I for the 72562 time
In I for the 72563 time
In I for the 72564 time
In I for the 72565 time
In I for the 72566 time
In I for the 72567 time
In I for the 72568 time
In I for the 72569 time
In I for the 72570 time
In I for the 72571 time
In I for the 72572 time
In I for the 72573 time
In I for the 72574 time
In I for the 725

In I for the 72878 time
In I for the 72879 time
In I for the 72880 time
In I for the 72881 time
In I for the 72882 time
In I for the 72883 time
In I for the 72884 time
In I for the 72885 time
In I for the 72886 time
In I for the 72887 time
In I for the 72888 time
In I for the 72889 time
In I for the 72890 time
In I for the 72891 time
In I for the 72892 time
In I for the 72893 time
In I for the 72894 time
In I for the 72895 time
In I for the 72896 time
In I for the 72897 time
In I for the 72898 time
In I for the 72899 time
In I for the 72900 time
In I for the 72901 time
In I for the 72902 time
In I for the 72903 time
In I for the 72904 time
In I for the 72905 time
In I for the 72906 time
In I for the 72907 time
In I for the 72908 time
In I for the 72909 time
In I for the 72910 time
In I for the 72911 time
In I for the 72912 time
In I for the 72913 time
In I for the 72914 time
In I for the 72915 time
In I for the 72916 time
In I for the 72917 time
In I for the 72918 time
In I for the 729

In I for the 73225 time
In I for the 73226 time
In I for the 73227 time
In I for the 73228 time
In I for the 73229 time
In I for the 73230 time
In I for the 73231 time
In I for the 73232 time
In I for the 73233 time
In I for the 73234 time
In I for the 73235 time
In I for the 73236 time
In I for the 73237 time
In I for the 73238 time
In I for the 73239 time
In I for the 73240 time
In I for the 73241 time
In I for the 73242 time
In I for the 73243 time
In I for the 73244 time
In I for the 73245 time
In I for the 73246 time
In I for the 73247 time
In I for the 73248 time
In I for the 73249 time
In I for the 73250 time
In I for the 73251 time
In I for the 73252 time
In I for the 73253 time
In I for the 73254 time
In I for the 73255 time
In I for the 73256 time
In I for the 73257 time
In I for the 73258 time
In I for the 73259 time
In I for the 73260 time
In I for the 73261 time
In I for the 73262 time
In I for the 73263 time
In I for the 73264 time
In I for the 73265 time
In I for the 732

In I for the 73574 time
In I for the 73575 time
In I for the 73576 time
In I for the 73577 time
In I for the 73578 time
In I for the 73579 time
In I for the 73580 time
In I for the 73581 time
In I for the 73582 time
In I for the 73583 time
In I for the 73584 time
In I for the 73585 time
In I for the 73586 time
In I for the 73587 time
In I for the 73588 time
In I for the 73589 time
In I for the 73590 time
In I for the 73591 time
In I for the 73592 time
In I for the 73593 time
In I for the 73594 time
In I for the 73595 time
In I for the 73596 time
In I for the 73597 time
In I for the 73598 time
In I for the 73599 time
In I for the 73600 time
In I for the 73601 time
In I for the 73602 time
In I for the 73603 time
In I for the 73604 time
In I for the 73605 time
In I for the 73606 time
In I for the 73607 time
In I for the 73608 time
In I for the 73609 time
In I for the 73610 time
In I for the 73611 time
In I for the 73612 time
In I for the 73613 time
In I for the 73614 time
In I for the 736

In [34]:
X

<73771x10 sparse matrix of type '<class 'numpy.float64'>'
	with 737710 stored elements in Compressed Sparse Row format>

In [35]:
Y

<73771x10 sparse matrix of type '<class 'numpy.float64'>'
	with 737710 stored elements in Compressed Sparse Row format>

In [52]:
#Function to find similar books

# Let's find similar books to the book whose book_id has been passed as a parameter to this function.
def give_similar(book_id,X,Y):
    
    # Get the book row for the book of which similar books are to be displayed 
    book_vec = Y[book_id].T

    # Calculate the similarity score between this book and other books
    # and select the top 10 most similar.
    scores = Y.dot(book_vec).toarray().reshape(1,-1)[0]
    top_10 = np.argsort(scores)[::-1][:10]

    books = []
    books_scores = []

    # Get and print the actual book names and scores
    for idx in top_10:
        books.append(books_lookup.book_title.loc[books_lookup.ISBN_id == str(idx)].iloc[0])
        books_scores.append(scores[idx])
    
    similar = pd.DataFrame({'Book': books})
    pd.set_option('display.max_colwidth', -1)
    print (similar)

In [53]:
give_similar(45911,X,Y)

                                                                             Book
0  "Harry Potter and the Order of the Phoenix (Book 5)"                          
1  "Chicken Soup for the Woman's Soul (Chicken Soup for the Soul Series (Paper))"
2  "Face the Fire (Three Sisters Island Trilogy)"                                
3  "Girl in Hyacinth Blue"                                                       
4  "Daughter of Fortune : A Novel (Oprah's Book Club (Hardcover))"               
5  "The Tale of the Body Thief (Vampire Chronicles (Paperback))"                 
6  "The Celestine Prophecy (Celestine Prophecy)"                                 
7  "Purity in Death"                                                             
8  "Life's Little Instruction Book (Life's Little Instruction Books (Paperback))"
9  "Strange Fits of Passion: A Novel"                                            


In [27]:
def recommend(USER_id, ratings_matrix, X, Y, no_of_books):
    """Recommend items for a given user given a trained model
    
        user_id (int): The id of the user we want to create recommendations for.    
        ratings_matrix (csr_matrix): Our original training data.
        X (csr_matrix): The trained user x features vectors
        Y (csr_matrix): The trained item x features vectors
        no_of_books (int): How many recommendations we want to return.
        
    Returns:
        recommendations (pandas.DataFrame): DataFrame with recommended books
    """
  
    # Get all interactions by the user
    user_interactions = ratings_matrix[USER_id,:].toarray()

    # We don't want to recommend books the user has already read and rated for. So let's
    # set them all to 0.
    user_interactions = user_interactions.reshape(-1) + 1    #Reshape to turn into 1D array
    user_interactions[user_interactions > 1] = 0

    #Now, calculate the recommendation 
    #dot-product of the user vectors with the item vectors.
    rec_vector = X[USER_id,:].dot(Y.T).toarray()

    # Let's scale our scores between 0 and 1 to make it all easier to interpret.
    min_max = MinMaxScaler()
    rec_vector_scaled = min_max.fit_transform(rec_vector.reshape(-1,1))[:,0]
    recommend_vector = user_interactions*rec_vector_scaled
   
    # Get all the books indices in order of recommendations (descending) and
    # select only the top "num_items" items. 
    book_index = np.argsort(recommend_vector)[::-1][:no_of_books]

    books = []
    scores = []

    # Loop through our recommended artist indicies and look up the actual book name
    
    for book in book_index:
        books.append(books_lookup.book_title.loc[books_lookup.ISBN_id == str(book)].iloc[0])
        scores.append(recommend_vector[book])

    # Create a new dataframe with recommended artist names and scores
    recommendations = pd.DataFrame({'Book': books, 'Score': scores})
    print(recommendations)



In [49]:
recommend(1156,ratings_matrix,X,Y,10)

                                                             Book     Score
0  "A Painted House"                                               1.000000
1  "The No. 1 Ladies' Detective Agency (Today Show Book Club #8)"  0.838920
2  "Snow Falling on Cedars"                                        0.829849
3  "The Bridges of Madison County"                                 0.795668
4  "The Hundred Secret Senses"                                     0.740169
5  "All I Really Need to Know"                                     0.703483
6  "Lonesome Dove"                                                 0.700446
7  "Harry Potter and the Sorcerer's Stone (Book 1)"                0.690732
8  "Tears of the Giraffe (No.1 Ladies Detective Agency)"           0.676075
9  "A Child Called \"It\": One Child's Courage to Survive"         0.672392


In [ ]:
import tkinter as tk
from tkinter.simpledialog import askstring, askinteger
from tkinter.messagebox import showerror


def display_1():
    # .get is used to obtain the current value
    # of entry_1 widget (This is always a string)
    num1 = entry_1.get()
    text = merged_books_df.loc[merged_books_df['Book_Title'] == '"' + num1 + '"','ISBN_ID']
    print(text[0])
    book_id_string = text[0]
    print(book_id_string)
    # Try convert a str to int
    # If unable eg. int('hello') or int('5.5')
    # then show an error.
    give_similar(book_id_string,user_vecs,item_vecs)
    

def display_2():
    num = entry_2.get()
    # Try convert a str to int
    # If unable eg. int('hello') or int('5.5')
    # then show an error.
    try:
       num = int(num)
    # ValueError is the type of error expected from this conversion
    except ValueError:
        #Display Error Window (Title, Prompt)
        showerror('Non-Int Error', 'Please enter an integer')
    else:
        recommend(num,ratings_matrix,user_vecs,item_vecs,10)

    
# Create the main window
root = tk.Tk()

# Create the widgets
entry_1 = tk.Entry(root)
btn_1 = tk.Button(root, text = "Submit Book title", command = display_1)

entry_2 = tk.Entry(root)
btn_2 = tk.Button(root, text = "Submit User title", command = display_2)

# Grid is used to add the widgets to root
# Alternatives are Pack and Placetex
entry_1.grid(row = 0, column = 0)
btn_1.grid(row = 1, column = 0)
entry_2.grid(row = 0, column = 1)
btn_2.grid(row = 1, column = 1)

#entry_1_string = str(entry_1)
#entry_1_string = '"' + entry_1_string + '"'
#text = merged_books_df.loc[merged_books_df['Book_Title'] == entry_1_string,'ISBN_ID']
#book_Id_entry = text.iloc[0]
#book_Id_entry

root.mainloop()

